**Step 1: Setting Up ExecuTorch**

In [1]:
!pip install executorch
# Testing release candidate
# !pip install --extra-index-url https://download.pytorch.org/whl/test/cpu executorch==0.6.0 torch==2.7.0 torchaudio==2.7.0 torchvision==0.22.0

In [2]:
# Installing dependencies for Llama
!pip install transformers accelerate sentencepiece huggingface_hub tiktoken torchtune tokenizers snakeviz lm_eval==0.4.5 blobfile

**Step 2. Download Llama 3.2 1B/3B models**

In [13]:
from huggingface_hub import login
login()

In [4]:
!huggingface-cli download meta-llama/Llama-3.2-1B --local-dir /content/models/Llama-3.2-1B --local-dir-use-symlinks False

/usr/local/lib/python3.11/dist-packages/huggingface_hub/commands/download.py:139: FutureWarning: Ignoring --local-dir-use-symlinks. Downloading to a local directory does not use symlinks anymore.
  warnings.warn(
Fetching 13 files:   0% 0/13 [00:00<?, ?it/s]Downloading 'generation_config.json' to '/content/models/Llama-3.2-1B/.cache/huggingface/download/3EVKVggOldJcKSsGjSdoUCN1AyQ=.2d73a6863086ff9d491c28e49df9fb697cd92c2b.incomplete'

consolidated.00.pth:   0% 0.00/2.47G [00:00<?, ?B/s]Downloading '.gitattributes' to '/content/models/Llama-3.2-1B/.cache/huggingface/download/wPaCkH-WbT7GsmxMKKrNZTV4nSM=.a6344aac8c09253b3b630fb776ae94478aa0275b.incomplete'


model.safetensors:   0% 0.00/2.47G [00:00<?, ?B/s]


config.json: 100% 843/843 [00:00<00:00, 3.77MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B/config.json



README.md: 100% 41.2k/41.2k [00:00<00:00, 24.5MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B/README.md



generation_config.json: 10

**Step 3: Export to ExecuTorch**

In [15]:
!cd /content/; python -m executorch.examples.models.llama.export_llama \
  --model "llama3_2" \
  --checkpoint /content/models/Llama-3.2-1B/original/consolidated.00.pth \
  --params /content/models/Llama-3.2-1B/original/params.json \
  -kv \
  --use_sdpa_with_kv_cache \
  -X \
  -d bf16 \
  --metadata '{"get_bos_id":128000, "get_eos_ids":[128009, 128001]}' \
  --output_name="llama3_2-1B.pte"

[INFO 2025-04-10 15:16:03,144 utils.py:162] NumExpr defaulting to 2 threads.
[INFO 2025-04-10 15:16:04,547 export_llama_lib.py:684] Applying quantizers: []
[INFO 2025-04-10 15:16:04,930 export_llama_lib.py:649] Checkpoint dtype: torch.bfloat16
[INFO 2025-04-10 15:16:04,931 quantized_kv_cache.py:277] Replacing KVCache with CustomKVCache. This modifies the model in place.
[INFO 2025-04-10 15:16:04,964 custom_ops.py:34] Looking for libcustom_ops_aot_lib.so in /usr/local/lib/python3.11/dist-packages/executorch/extension/llm/custom_ops
[INFO 2025-04-10 15:16:04,966 custom_ops.py:39] Loading custom ops library: /usr/local/lib/python3.11/dist-packages/executorch/extension/llm/custom_ops/libcustom_ops_aot_lib.so
[INFO 2025-04-10 15:16:04,980 builder.py:173] Model after source transforms: Transformer(
  (tok_embeddings): Embedding(128256, 2048)
  (rope): Rope(
    (apply_rotary_emb): RotaryEmbedding()
  )
  (layers): ModuleList(
    (0-15): 16 x TransformerBlock(
      (attention): AttentionMHA

In [16]:
!mv ./llama3_2-1B.pte /content/models/Llama-3.2-1B/original/

**Step 4: Upload to HF**

In [17]:
!huggingface-cli upload executorch-community/Llama-3.2-1B-ET /content/models/Llama-3.2-1B/original/ --exclude="*.pth"

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
Start hashing 3 files.
Finished hashing 3 files.
llama3_2-1B.pte: 100% 2.47G/2.47G [01:02<00:00, 39.3MB/s]
Removing 2 file(s) from commit that have not changed.
https://huggingface.co/executorch-community/Llama-3.2-1B-ET/tree/main/.
